In [ ]:
!pip install -q kaggle

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import os
os.environ['KAGGLE_USERNAME'] = ""
os.environ['KAGGLE_KEY'] = ""

In [ ]:
!kaggle competitions download -c ss3-nlp-cmsk-chatbot

ss3-nlp-cmsk-chatbot.zip: Skipping, found more recently modified local copy (use --force to force download)


In [ ]:
!unzip ss3-nlp-cmsk-chatbot.zip

### import library

In [ ]:
import pandas as pd 
import numpy as np

In [ ]:
context_path = "/content/context/"
doc_path = "/content/documents(1).csv"
bm25_path = "/content/final_test_top5.csv"
test_path = "/content/final_test.csv"

In [ ]:
test_df = pd.read_csv(test_path)
test_df

id                                           question
0      1  ตลาดหลักทรัพย์ได้กำหนดราคาสูงสุดต่ำสุดของ Warr...
1      2                 ลักษณะแนวทางในการระดมทุนมีอะไรบ้าง
2      3  Gross Price หรือ Dirty Price มีวิธีการจ่ายดอกเ...
3      4  รายได้จากการลงทุนต่อ (Reinvestment income) คือ...
4      5  ตัวอย่างลำดับเหตุการณ์ที่เกี่ยวข้องกับการจ่ายเ...
..   ...                                                ...
270  271  ผู้จัดอันดับกองทุนรวมที่ได้รับอนุญาตจาก ก.ล.ต....
271  272               สูตรการคำนวณ Cash Settlement คืออะไร
272  273      ข้อดีของการประเมินมูลค่าด้วย PB Ratio คืออะไร
273  274           การรวมหุ้น (Reverse Stock Split) คืออะไร
274  275    งบประจำงวด 1 ปี ฉบับตรวจสอบ กำหนดส่งภายในกี่วัน

[275 rows x 2 columns]

In [ ]:
doc = pd.read_csv(doc_path)
doc.head()

file  cid
0  1345137.txt    0
1  1345157.txt    1
2  1345179.txt    2
3  1345178.txt    3
4  1345146.txt    4

In [ ]:
bm25 = pd.read_csv(bm25_path)
bm25.head()

id                                           question  top1  top2  top3  \
0   1  ตลาดหลักทรัพย์ได้กำหนดราคาสูงสุดต่ำสุดของ Warr...    26     0    33   
1   2                 ลักษณะแนวทางในการระดมทุนมีอะไรบ้าง    18    10     8   
2   3  Gross Price หรือ Dirty Price มีวิธีการจ่ายดอกเ...    34    29     0   
3   4  รายได้จากการลงทุนต่อ (Reinvestment income) คือ...    22    21    19   
4   5  ตัวอย่างลำดับเหตุการณ์ที่เกี่ยวข้องกับการจ่ายเ...    17    24    39   

   top4  top5  
0    48    10  
1    47    30  
2    33    13  
3    49    36  
4    16     7

In [ ]:
context_list = []
for filename in os.listdir(context_path):
  full_path = context_path + str(filename)
  if filename.endswith(".txt"):
    file = open(full_path,"r",encoding="utf8", errors='ignore')
    raw_text = file.read()
    context_list.append([filename, raw_text])

In [ ]:
df_context = pd.DataFrame(context_list, columns=['filename', 'context'])
df_context.head()

filename                                            context
0  1345159.txt  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n2.\tผู้ท...
1  1345143.txt  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...
2  1345188.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n8.\tการกำกับดูแ...
3  1345198.txt  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...
4  1345197.txt  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...

In [ ]:
doc_bm25 = doc.merge(df_context, left_on="file", right_on="filename", how='left')
doc_bm25.head()

file  cid     filename  \
0  1345137.txt    0  1345137.txt   
1  1345157.txt    1  1345157.txt   
2  1345179.txt    2  1345179.txt   
3  1345178.txt    3  1345178.txt   
4  1345146.txt    4  1345146.txt   

                                             context  
0  การซื้อขายตราสารหนี้ในไทย\n\n2.\tกระบวกการออกต...  
1  การวิเคราะห์และกลยุทธ์การลงทุนในกองทุนรวม\n\n3...  
2  ตราสารที่เชื่อมโยงกับตราสารทุน\n\n5.\tใบสำคัญแ...  
3  ตราสารที่เชื่อมโยงกับตราสารทุน\n\n4.\tใบสำคัญแ...  
4  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...

In [ ]:
query_df = bm25[["question", "top1"]]
query_df.head()

question  top1
0  ตลาดหลักทรัพย์ได้กำหนดราคาสูงสุดต่ำสุดของ Warr...    26
1                 ลักษณะแนวทางในการระดมทุนมีอะไรบ้าง    18
2  Gross Price หรือ Dirty Price มีวิธีการจ่ายดอกเ...    34
3  รายได้จากการลงทุนต่อ (Reinvestment income) คือ...    22
4  ตัวอย่างลำดับเหตุการณ์ที่เกี่ยวข้องกับการจ่ายเ...    17

In [ ]:
temp_df = bm25[["question", "top1"]]
contextfile_list = []
context_list = []
for top in temp_df["top1"]:
  contextfile_list.append(doc_bm25["file"].iloc[top])
  context_list.append(doc_bm25["context"].iloc[top])

In [ ]:
query_df["file1"] = contextfile_list
query_df["context1"] = context_list
query_df.head()

<ipython-input-25-5d4181af6262>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  query_df["file1"] = contextfile_list
<ipython-input-25-5d4181af6262>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  query_df["context1"] = context_list


question  top1        file1  \
0  ตลาดหลักทรัพย์ได้กำหนดราคาสูงสุดต่ำสุดของ Warr...    26  1345184.txt   
1                 ลักษณะแนวทางในการระดมทุนมีอะไรบ้าง    18  1345182.txt   
2  Gross Price หรือ Dirty Price มีวิธีการจ่ายดอกเ...    34  1345143.txt   
3  รายได้จากการลงทุนต่อ (Reinvestment income) คือ...    22  1345172.txt   
4  ตัวอย่างลำดับเหตุการณ์ที่เกี่ยวข้องกับการจ่ายเ...    17  1345196.txt   

                                            context1  
0  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n4.\tหน่วยการซื้...  
1  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n2.\tกระบวนการ ว...  
2  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...  
3  ความรู้พื้นฐานของตราสารหนี้\n\n4.\tผลตอบแทนจาก...  
4  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...

### Modeling

In [ ]:
train_df = pd.read_csv("/content/train.csv")
iapp_df = pd.read_csv("/content/drive/MyDrive/NLP/iapp_thaiqa_datasets.csv")
#iapp_df = iapp_df.drop('Unnamed: 0',axis=1)

## get text from Context to dataframe.
context_path = "/content/context/"
context_list = []
for filename in os.listdir(context_path):
  full_path = context_path + str(filename)
  if filename.endswith(".txt"):
    file = open(full_path,"r",encoding="utf8", errors='ignore')
    raw_text = file.read()
    context_list.append([filename, raw_text])

## df_context ##
df_context = pd.DataFrame(context_list, columns=['filename', 'context'])

In [ ]:
remove_index = []
for i in range(iapp_df.shape[0]):
  try:
    start = iapp_df["cleansing"][i][iapp_df.loc[i, "answer_start"]]
    end = iapp_df["cleansing"][i][iapp_df.loc[i, "answer_end"]]
  except: 
    remove_index.append(i)

In [ ]:
iapp_df = iapp_df.drop(iapp_df.index[remove_index], axis = 0)
iapp_df = iapp_df.reset_index(drop=True)
iapp_df

cleansing  \
0      พัทธ์ธีรา ศรุติพงศ์โภคิน (เกิด 3 ธันวาคม พ.ศ. ...   
1      พัทธ์ธีรา ศรุติพงศ์โภคิน (เกิด 3 ธันวาคม พ.ศ. ...   
2      พัทธ์ธีรา ศรุติพงศ์โภคิน (เกิด 3 ธันวาคม พ.ศ. ...   
3      พัทธ์ธีรา ศรุติพงศ์โภคิน (เกิด 3 ธันวาคม พ.ศ. ...   
4      คลีโอพัตราที่ 7 ฟิโลพาเธอร์ (กรีก: Κλεοπάτρα θ...   
...                                                  ...   
10903  เรวิญานันท์ ทาเกิด เรวิญานันท์ ทาเกิด หรือ เบญ...   
10904  กูดฟีลลิง (เพลง) กูดฟิลลิง () เป็นเพลงของนักร้...   
10905  ปภัสรา เตชะไพบูลย์ ดร.ปภัสรา เตชะไพบูลย์ มีชื่...   
10906  ปีเตอร์ ดรักเกอร์ ปีเตอร์ เฟอร์ดินานด์ ดรักเกอ...   
10907  เทือกเขาตะนาวศรี เทือกเขาตะนาวศรี (; ) เป็นชื่...   

                                                question  \
0              พัทธ์ธีรา ศรุติพงศ์โภคิน เกิดวันที่เท่าไร   
1             พัทธ์ธีรา ศรุติพงศ์โภคิน มีฃื่อเล่นว่าอะไร   
2                   พัทธ์ธีรา ศรุติพงศ์โภคิน ทำอาชีพอะไร   
3       พัทธ์ธีรา ศรุติพงศ์โภคิน จบการศึกษาจากประเทศอะไร   
4                               บิดาของคลีโอพัตราเป็นใคร   
...                                                  ...   
10903  เรวิญานันท์ ทาเกิด หรือ เบญ บ้านเกิดอยู่จังหวั...   
10904                      กูดฟิลลิงเป็นเพลงจากอัลบั้มใด   
10905  กบ ปภัสรา ชีวิตส่วนตัวได้สมรสกับนักการเมืองท่านใด   
10906                พ่อของปีเตอร์ ดรักเกอร์ ทำอาชีพอะไร   
10907                 แม่น้ำใดไหลตัดผ่านเทือกเขาตะนาวศรี   

              ans_cleansing  answer_start  answer_end  
0       3 ธันวาคม พ.ศ. 2533            31          50  
1                        อร            68          70  
2         นักแสดงหญิงชาวไทย            75          92  
3          ประเทศนิวซีแลนด์           139         155  
4      ทอเลมีที่ 12 ออเลติส           319         339  
...                     ...           ...         ...  
10903          จังหวัดลำพูน           398         410  
10904            ไวลด์วันส์           198         208  
10905  นายพรเทพ เตชะไพบูลย์           638         658  
10906              ทนายความ           951         959  
10907     แควใหญ่และแควน้อย           925         942  

[10908 rows x 5 columns]

In [ ]:
iapp_df["file"] = "123456.txt"

### QG
cr. https://www.kaggle.com/code/tanatiparchwamety/colab-22p22c0134-scg-qa

In [ ]:
df_train_orig = pd.read_csv("train.csv")
what_how_qword = ['อะไร','คือ'] 
amount_qword = ['กี่','แค่ไหน','เท่าไร','เท่าไหร่','เท่าใด']
when_qword = ['เมื่อใด','เมื่อไร','เวลาใด','เวลาไหน','วันไหน','ปีใด','ปีไหน']
where_qword = ['ที่ใด','ที่ไหน']
where_url_qword = ['link ไหน','link อะไร','URL ใด','URL อะไร','เว็บไหน','เว็บอะไร','ได้ที่ไหน']
who_qword = ['ใคร']

def get_question_type(qa_dataframe, folder='train'):
  tmp = qa_dataframe.copy()
  tmp['question_type'] = ""
  tmp.loc[(tmp['question'].str.contains('|'.join(what_how_qword))), 'question_type']      = "what_how"
  tmp.loc[(tmp['question'].str.contains('|'.join(amount_qword))), 'question_type']        = "amount"
  tmp.loc[(tmp['question'].str.contains('เกี่ยว')), 'question_type']                        = "" #revert bug keyword

  tmp.loc[(tmp['question'].str.contains('|'.join(when_qword))), 'question_type']          = "when"
  tmp.loc[(tmp['question'].str.contains('|'.join(where_qword))), 'question_type']         = "where"
  tmp.loc[(tmp['question'].str.contains('|'.join(where_url_qword))), 'question_type']     = "where_url"
  tmp.loc[(tmp['question'].str.contains('|'.join(who_qword))), 'question_type']           = "who"
  tmp.loc[(tmp['question_type']==""), 'question_type']                                    = "what_how"
  return tmp

In [ ]:
tmp = get_question_type(df_train_orig, folder='train')
tmp['question_type'].value_counts()

what_how    371
amount       22
who           8
when          7
where         2
Name: question_type, dtype: int64

In [ ]:
augment_qword = { "what_how"  : what_how_qword ,
                  "amount"    : amount_qword,
                  "who"       : who_qword,
                  "when"      : when_qword,
                  "where_url" : where_url_qword,
                  "where"     : where_qword}
augment_dict = {}


for a in augment_qword.keys():
  augment_dict["tmp_"+a]                = tmp[tmp['question_type']==a]
  augment_dict["res_"+a]                = tmp[tmp['question_type']==a]
  augment_dict["res_"+a]['question']    = augment_dict["res_"+a]['question'].str.replace('|'.join(augment_qword[a]), '')
# augment_dict["tmp_where"]
# augment_dict["res_where"]


for a in augment_qword.keys():
  for kw in augment_qword[a]:
    augment_dict["tmp_"+a]['question'] = augment_dict["tmp_"+a]['question'].str.replace('|'.join(augment_qword[a]), '')
    augment_dict["tmp_"+a]['question'] = augment_dict["tmp_"+a]['question'] + kw
    augment_dict["res_"+a] = pd.concat([augment_dict["res_"+a], augment_dict["tmp_"+a]], ignore_index=True)
    augment_dict["tmp_"+a]['question'] = augment_dict["tmp_"+a]['question'].str.replace('|'.join(augment_qword[a]), '')
    augment_dict["tmp_"+a]['question'] = kw + augment_dict["tmp_"+a]['question']
    augment_dict["res_"+a] = pd.concat([augment_dict["res_"+a], augment_dict["tmp_"+a]], ignore_index=True)

#augment_dict["res_amount"]

<ipython-input-32-b3e9a68a5d9d>:13: FutureWarning: The default value of regex will change from True to False in a future version.
  augment_dict["res_"+a]['question']    = augment_dict["res_"+a]['question'].str.replace('|'.join(augment_qword[a]), '')
<ipython-input-32-b3e9a68a5d9d>:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  augment_dict["res_"+a]['question']    = augment_dict["res_"+a]['question'].str.replace('|'.join(augment_qword[a]), '')
<ipython-input-32-b3e9a68a5d9d>:20: FutureWarning: The default value of regex will change from True to False in a future version.
  augment_dict["tmp_"+a]['question'] = augment_dict["tmp_"+a]['question'].str.replace('|'.join(augment_qword[a]), '')
<ipython-input-32-b3e9a68a5d9d>:20: SettingWithCopyWarni

In [ ]:
augment_train = pd.concat([augment_dict["res_what_how"], \
                           augment_dict["res_amount"], \
                           augment_dict["res_who"], \
                           augment_dict["res_when"], \
                           augment_dict["res_where_url"], \
                           augment_dict["res_where"], \
                           ], ignore_index=True)
augment_train.tail()

file                                           question  \
2231  1345138.txt                ที่ใดผู้ค้าตราสารหนี้สร้างรายได้จาก   
2232  1345160.txt  รายได้หลักของกองทุนรวมโครงสร้างพื้นฐานมาจากที่ไหน   
2233  1345138.txt               ผู้ค้าตราสารหนี้สร้างรายได้จากที่ไหน   
2234  1345160.txt  ที่ไหนรายได้หลักของกองทุนรวมโครงสร้างพื้นฐานมาจาก   
2235  1345138.txt               ที่ไหนผู้ค้าตราสารหนี้สร้างรายได้จาก   

                                           answer  answer_start  answer_end  \
2231            สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366        2398   
2232  การเก็บค่าเช่าหรือค่าบริการโครงสร้างพื้นฐาน         11387       11429   
2233            สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366        2398   
2234  การเก็บค่าเช่าหรือค่าบริการโครงสร้างพื้นฐาน         11387       11429   
2235            สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366        2398   

     question_type  
2231         where  
2232         where  
2233         where  
2234         where  
2235         where

In [ ]:
augment_train = augment_train.drop('question_type',axis=1)

### Cleansing

In [ ]:
def text_cleansing(text):
    #  regex = re.compile('[''\\r\\t\t\\n\\n + \n\n]')
    #  text = normalize(text)
    #  text = regex.sub(" ", text) # remove punctuation
    #  text = re.sub(r'\d+\.\d+', '', text)
    #  text = re.sub(r'\d+\.', '', text)
    #  text = re.sub(r'\d+\)', '', text)
    #  #text = re.sub(r'\d+\)', '', text)
    #  text = re.sub("[@_!#$^*<>?\"/\|}{~]",'',text)
   text = text
   #text = re.sub(r'(?:http|ftp|https)://(?:[\w_-]+(?:(?:\.[\w_-]+)+))(?:[\w.,@?^=%&:/~+#-]*[\w@?^=%&/~+#-])?',' ',text)
   return text

In [ ]:
## Add cleansing column in df_context
context_cleansing = [text_cleansing(x) for x in df_context['context']]
df_context['cleansing'] = context_cleansing
df_context

filename                                            context  \
0   1345159.txt  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n2.\tผู้ท...   
1   1345143.txt  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...   
2   1345188.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n8.\tการกำกับดูแ...   
3   1345198.txt  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
4   1345197.txt  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
5   1345160.txt  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...   
6   1345180.txt  ตราสารที่เชื่อมโยงกับตราสารทุน\n\n6.\tใบสำคัญแ...   
7   1345178.txt  ตราสารที่เชื่อมโยงกับตราสารทุน\n\n4.\tใบสำคัญแ...   
8   1345136.txt  การซื้อขายตราสารหนี้ในไทย\n\n1.\tตลาดตราสารหนี...   
9   1345179.txt  ตราสารที่เชื่อมโยงกับตราสารทุน\n\n5.\tใบสำคัญแ...   
10  1345170.txt  ความรู้พื้นฐานของตราสารหนี้\n\n2.\tความแตกต่าง...   
11  1345201.txt  ผลตอบแทนและความเสี่ยงของกองทุนรวม\n\n3.\tความเ...   
12  1345172.txt  ความรู้พื้นฐานของตราสารหนี้\n\n4.\tผลตอบแทนจาก...   
13  1345142.txt  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...   
14  1345190.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n10.\tดัชนีหลักท...   
15  1345171.txt  ความรู้พื้นฐานของตราสารหนี้\n\n3.\tองค์ประกอบ ...   
16  1345147.txt  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...   
17  1345192.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n12.\tภาษีของการ...   
18  1345199.txt  ผลตอบแทนและความเสี่ยงของกองทุนรวม\n\n1.\tภาพรว...   
19  1345139.txt  การซื้อขายตราสารหนี้ในไทย\n\n4.\tดัชนีตราสารหน...   
20  1345158.txt  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n1.\tลักษ...   
21  1345195.txt  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
22  1345138.txt  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   
23  1345181.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n1.\tระบบการซื้อ...   
24  1345175.txt  ตราสารที่เชื่อมโยงกับตราสารทุน\n\n1.\tความหมาย...   
25  1345194.txt  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
26  1345183.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n3.\tเวลาในการซื...   
27  1345202.txt  ผลตอบแทนและความเสี่ยงของกองทุนรวม\n\n4.\tการวั...   
28  1345157.txt  การวิเคราะห์และกลยุทธ์การลงทุนในกองทุนรวม\n\n3...   
29  1345200.txt  ผลตอบแทนและความเสี่ยงของกองทุนรวม\n\n2.\tผลตอบ...   
30  1345196.txt  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
31  1345137.txt  การซื้อขายตราสารหนี้ในไทย\n\n2.\tกระบวกการออกต...   
32  1345187.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n7.\tการเปิดบัญช...   
33  1345150.txt  การประเมินมูลค่าหุ้นสามัญ\n\n3.\tการประเมินมูล...   
34  1345176.txt  ตราสารที่เชื่อมโยงกับตราสารทุน\n\n2.\tใบสำคัญแ...   
35  1345189.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n9.\tข้อมูลที่บร...   
36  1345145.txt  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...   
37  1345186.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n6.\tแผนสำรองกรณ...   
38  1345182.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n2.\tกระบวนการ ว...   
39  1345141.txt  การซื้อขายตราสารหนี้ในไทย\n\n6.\tภาษีของตราสาร...   
40  1345154.txt  การประเมินมูลค่าหุ้นสามัญ\n\n5.\tกลยุทธ์การลงท...   
41  1345191.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n11.\tข้อมูลจากต...   
42  1345173.txt  ความรู้พื้นฐานของตราสารหนี้\n\n5.\tประเภทของตร...   
43  1345144.txt  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...   
44  1345174.txt  ความรู้พื้นฐานของตราสารหนี้\n\n6.\tประโยชน์ของ...   
45  1345156.txt  การวิเคราะห์และกลยุทธ์การลงทุนในกองทุนรวม\n\n2...   
46  1345149.txt  การประเมินมูลค่าหุ้นสามัญ\n\n2. วิธีการประเมิน...   
47  1345161.txt  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n4.\tภาษี...   
48  1345184.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n4.\tหน่วยการซื้...   
49  1345153.txt  การประเมินมูลค่าหุ้นสามัญ\n\n4.\tRelative Valu...   
50  1345193.txt  ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
51  1345146.txt  การประเมินมูลค่าและอัตราผลตอบแทนของตราสารหนี้\...   
52  1345177.txt  ตราสารที่เชื่อมโยงกับตราสารทุน\n\n3.\tใบสำคัญแ...   
53  1345185.txt  ตลาดหลักทรัพย์แห่งประเทศไทย\n\n5.\tการหยุดการซ...   
54  1345140.txt  การซื้อขายตราสารหนี้ในไทย\n\n5.\tข้อมูลและแหล่...   
55  1345155.txt  การวิเคราะห์และกลยุทธ์การลงทุนในกองทุนรวม\n\n1...   
56  1345169.txt  

In [ ]:
#merge dataframe
train_df_mearge = augment_train.merge(df_context, left_on="file", right_on="filename", how="left")
train_df_mearge

file                                           question  \
0     1345195.txt             Penny Stock หุ้นเหรียญ มีลักษณะอย่างไร   
1     1345200.txt                                         ราคาต้นงวด   
2     1345158.txt  หนังสือชี้ชวนส่วนสรุปข้อมูลสำคัญ (Fund Fact Sh...   
3     1345171.txt                              ข้อสัญญา (Covenants)    
4     1345185.txt                                                XT    
...           ...                                                ...   
2231  1345138.txt                ที่ใดผู้ค้าตราสารหนี้สร้างรายได้จาก   
2232  1345160.txt  รายได้หลักของกองทุนรวมโครงสร้างพื้นฐานมาจากที่ไหน   
2233  1345138.txt               ผู้ค้าตราสารหนี้สร้างรายได้จากที่ไหน   
2234  1345160.txt  ที่ไหนรายได้หลักของกองทุนรวมโครงสร้างพื้นฐานมาจาก   
2235  1345138.txt               ที่ไหนผู้ค้าตราสารหนี้สร้างรายได้จาก   

                                                 answer  answer_start  \
0     *\tหุ้นที่มีราคาซื้อขายต่อหน่วยต่ำ (ในสหรัฐฯ ค...          3019   
1                                ราคาต้นทุนหรือราคาซื้อ           501   
2                 เอกสารที่ให้ข้อมูลที่สำคัญกับผู้ลงทุน          1116   
3     พันธสัญญาที่ผู้ออกตราสารให้ผู้ลงทุนเพื่อเพิ่มค...           892   
4               ผู้ซื้อหลักทรัพย์จะไม่มีสิทธิได้รับ TSR          1165   
...                                                 ...           ...   
2231                  สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366   
2232        การเก็บค่าเช่าหรือค่าบริการโครงสร้างพื้นฐาน         11387   
2233                  สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366   
2234        การเก็บค่าเช่าหรือค่าบริการโครงสร้างพื้นฐาน         11387   
2235                  สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366   

      answer_end     filename  \
0           3138  1345195.txt   
1            522  1345200.txt   
2           1152  1345158.txt   
3            971  1345171.txt   
4           1203  1345185.txt   
...          ...          ...   
2231        2398  1345138.txt   
2232       11429  1345160.txt   
2233        2398  1345138.txt   
2234       11429  1345160.txt   
2235        2398  1345138.txt   

                                                context  \
0     ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
1     ผลตอบแทนและความเสี่ยงของกองทุนรวม\n\n2.\tผลตอบ...   
2     ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n1.\tลักษ...   
3     ความรู้พื้นฐานของตราสารหนี้\n\n3.\tองค์ประกอบ ...   
4     ตลาดหลักทรัพย์แห่งประเทศไทย\n\n5.\tการหยุดการซ...   
...                                                 ...   
2231  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   
2232  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...   
2233  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   
2234  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...   
2235  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   

                                              cleansing  
0     ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...  
1     ผลตอบแทนและความเสี่ยงของกองทุนรวม\n\n2.\tผลตอบ...  
2     ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n1.\tลักษ...  
3     ความรู้พื้นฐานของตราสารหนี้\n\n3.\tองค์ประกอบ ...  
4     ตลาดหลักทรัพย์แห่งประเทศไทย\n\n5.\tการหยุดการซ...  
...                                                 ...  
2231  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...  
2232  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...  
2233  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...  
2234  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...  
2235  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...  

[2236 rows x 8 columns]

In [ ]:
# Clean answer
ans_cleansing = [text_cleansing(x) for x in train_df_mearge['answer']]
train_df_mearge['ans_cleansing'] = ans_cleansing
train_df_mearge

file                                           question  \
0     1345195.txt             Penny Stock หุ้นเหรียญ มีลักษณะอย่างไร   
1     1345200.txt                                         ราคาต้นงวด   
2     1345158.txt  หนังสือชี้ชวนส่วนสรุปข้อมูลสำคัญ (Fund Fact Sh...   
3     1345171.txt                              ข้อสัญญา (Covenants)    
4     1345185.txt                                                XT    
...           ...                                                ...   
2231  1345138.txt                ที่ใดผู้ค้าตราสารหนี้สร้างรายได้จาก   
2232  1345160.txt  รายได้หลักของกองทุนรวมโครงสร้างพื้นฐานมาจากที่ไหน   
2233  1345138.txt               ผู้ค้าตราสารหนี้สร้างรายได้จากที่ไหน   
2234  1345160.txt  ที่ไหนรายได้หลักของกองทุนรวมโครงสร้างพื้นฐานมาจาก   
2235  1345138.txt               ที่ไหนผู้ค้าตราสารหนี้สร้างรายได้จาก   

                                                 answer  answer_start  \
0     *\tหุ้นที่มีราคาซื้อขายต่อหน่วยต่ำ (ในสหรัฐฯ ค...          3019   
1                                ราคาต้นทุนหรือราคาซื้อ           501   
2                 เอกสารที่ให้ข้อมูลที่สำคัญกับผู้ลงทุน          1116   
3     พันธสัญญาที่ผู้ออกตราสารให้ผู้ลงทุนเพื่อเพิ่มค...           892   
4               ผู้ซื้อหลักทรัพย์จะไม่มีสิทธิได้รับ TSR          1165   
...                                                 ...           ...   
2231                  สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366   
2232        การเก็บค่าเช่าหรือค่าบริการโครงสร้างพื้นฐาน         11387   
2233                  สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366   
2234        การเก็บค่าเช่าหรือค่าบริการโครงสร้างพื้นฐาน         11387   
2235                  สร้างรายได้จากส่วนต่างราคาซื้อขาย          2366   

      answer_end     filename  \
0           3138  1345195.txt   
1            522  1345200.txt   
2           1152  1345158.txt   
3            971  1345171.txt   
4           1203  1345185.txt   
...          ...          ...   
2231        2398  1345138.txt   
2232       11429  1345160.txt   
2233        2398  1345138.txt   
2234       11429  1345160.txt   
2235        2398  1345138.txt   

                                                context  \
0     ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
1     ผลตอบแทนและความเสี่ยงของกองทุนรวม\n\n2.\tผลตอบ...   
2     ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n1.\tลักษ...   
3     ความรู้พื้นฐานของตราสารหนี้\n\n3.\tองค์ประกอบ ...   
4     ตลาดหลักทรัพย์แห่งประเทศไทย\n\n5.\tการหยุดการซ...   
...                                                 ...   
2231  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   
2232  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...   
2233  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   
2234  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...   
2235  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   

                                              cleansing  \
0     ประเภทของธุรกิจและที่มาของเงินทุนในการทำธุรกิจ...   
1     ผลตอบแทนและความเสี่ยงของกองทุนรวม\n\n2.\tผลตอบ...   
2     ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n1.\tลักษ...   
3     ความรู้พื้นฐานของตราสารหนี้\n\n3.\tองค์ประกอบ ...   
4     ตลาดหลักทรัพย์แห่งประเทศไทย\n\n5.\tการหยุดการซ...   
...                                                 ...   
2231  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   
2232  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...   
2233  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   
2234  ความรู้เบื้องต้นเกี่ยวกับกองทุนรวม\n\n3.\tประเ...   
2235  การซื้อขายตราสารหนี้ในไทย\n\n3.\tผู้เกี่ยวข้อง...   

                                          ans_cleansing  
0     *\tหุ้นที่มีราคาซื้อขายต่อหน่วยต่ำ (ในสหรัฐฯ ค...  
1                                ราคาต้นทุนหรือราคาซื้อ  
2                 เอกสารที่ให้ข้อมูลที่สำคัญกับผู้ลงทุน  
3     พันธสัญญาที่ผู้ออกตราสารให้ผู้ลงทุนเพื่อเพิ่มค...  
4               ผู้ซื้อหลักทรัพย์จะไม่มีสิทธิได้รับ TSR  
...                                                 ...  
2231                  สร้างรายได้จากส่วนต่างราคาซื

In [ ]:
train_df_clean = train_df_mearge[["file", "cleansing", "question", "ans_cleansing", "answer_start", "answer_end"]]

### Train/Test Split

In [ ]:
train_df_clean = pd.concat([train_df_clean,iapp_df],axis = 0)

In [ ]:
train_df_clean['answer_start'] = pd.to_numeric(train_df_clean['answer_start'], errors='coerce')
train_df_clean['answer_end'] = pd.to_numeric(train_df_clean['answer_end'], errors='coerce')
train_df_clean = train_df_clean.dropna(subset=['answer_start'])
train_df_clean = train_df_clean.dropna(subset=['answer_end'])
train_df_clean = train_df_clean.reset_index(drop=True)

In [ ]:
convert_dict = {'answer_start': int,
                'answer_end': int,
                'ans_cleansing' : str,
                'cleansing' : str
                }
 
train_df_clean = train_df_clean.astype(convert_dict)

In [ ]:
from sklearn.model_selection import train_test_split

train, val = train_test_split(train_df_clean, test_size=0.2, random_state=42)
train, test = train_test_split(train, test_size=0.1, random_state=42)
test, mini_local_test = train_test_split(test, test_size=0.4, random_state=42)

### check size
print("all shape:", train_df_clean.shape)
print("train shape:", train.shape)
print("evaluation shape:", val.shape)
print("test shape:", test.shape)
print("local test:", mini_local_test.shape)

all shape: (13144, 6)
train shape: (9463, 6)
evaluation shape: (2629, 6)
test shape: (631, 6)
local test: (421, 6)


In [ ]:
import json
#from pythainlp.tokenize import word_tokenize

In [ ]:
def convert_to_simpletransformer_format(df):
  all = {}

  for (idx, row) in df.iterrows():
    answer = row["ans_cleansing"]
    if (row["file"] not in all):
      # context = " ".join(word_tokenize(row["token"],engine="newmm-safe"))
      context = row["cleansing"]
      all[row["file"]] = {"context": context, "qas":[]}
      # question_text = " ".join(word_tokenize(row["question_clean"],engine="newmm-safe"))
      # answer_text = " ".join(word_tokenize(row["answer_clean"],engine="newmm-safe"))
      question_text = row["question"]
      answer_text = row["ans_cleansing"]
      answer_start = row["answer_start"]
      answer_end = row["answer_end"]
      answer_diff = int(answer_end) - int(answer_start)
      if answer_diff <= 1:
        im_bool = True
      else:
        im_bool = False
        
      try:
        all[row["file"]]["qas"].append({
          "id": idx,
          "is_impossible": im_bool,
          "question":question_text,
          "answers": [{"text":answer_text, "answer_start": answer_start,"answer_end" : answer_end }]

      })
      except Exception as e:
        print("Context:" +all[row["file"]]["context"])
        print("Answer:" +answer_text)
        print("Exception:" +str(e))

  return list(all.values())

In [ ]:
train_data = convert_to_simpletransformer_format(train)
validation_data = convert_to_simpletransformer_format(val)
test_data = convert_to_simpletransformer_format(test)

### Model

In [ ]:
!pip install simpletransformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.5/250.5 KB 19.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 KB 5.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 92.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 84.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 100.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 73.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 469.0/469.0 KB 47.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 113.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.3/190.3 KB 23.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 184.3/184.3 KB 19.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━

In [ ]:
from simpletransformers.question_answering import QuestionAnsweringModel, QuestionAnsweringArgs
import logging
import torch

# Configure the model
model_args = QuestionAnsweringArgs()

model_args.learning_rate = 3e-5
model_args.num_train_epochs = 15
model_args.max_seq_length = 512
model_args.doc_stride = 64
model_args.overwrite_output_dir = True
model_args.evaluate_during_training = True
model_args.reprocess_input_data = False
model_args.train_batch_size = 16
model_args.gradient_accumulation_steps = 1
model_args.null_score_diff_threshold = 0.9
model_args.manual_seed = 100
#model_args.save_steps = 5000


model = QuestionAnsweringModel(
    "xlmroberta", "deepset/xlm-roberta-large-squad2", args=model_args, use_cuda=torch.cuda.is_available()
)

# Train the model
model.train_model(train_data, eval_data=validation_data)

# Evaluate the model
result, texts = model.eval_model(test_data)

add example index and unique id: 100%|██████████| 30/30 [00:00<00:00, 83330.54it/s]


Epoch:   0%|          | 0/15 [00:00<?, ?it/s]

Running Epoch 0 of 15:   0%|          | 0/21 [00:00<?, ?it/s]

/usr/local/lib/python3.8/dist-packages/torch/optim/lr_scheduler.py:138: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  warnings.warn("Detected call of `lr_scheduler.step()` before `optimizer.step()`. "

convert squad examples to features: 100%|██████████| 29/29 [00:13<00:00,  2.11it/s]

add example index and unique id: 100%|██████████| 29/29 [00:00<00:00, 79603.94it/s]


Running Evaluation:   0%|          | 0/42 [00:00<?, ?it/s]

...

Running Evaluation:   0%|          | 0/42 [00:00<?, ?it/s]

Running Epoch 14 of 15:   0%|          | 0/21 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/42 [00:00<?, ?it/s]

add example index and unique id: 100%|██████████| 27/27 [00:00<00:00, 70690.52it/s]


Running Evaluation:   0%|          | 0/40 [00:00<?, ?it/s]

### Prediction

In [ ]:
idx = 0
file_list = []
ans_list = []
prob_list = []
question_list = []

for idx in range(len(query_df)):
  to_predict = [
      {
          "context": query_df["context1"].iloc[idx],
          "qas": [
              {
                  "question": query_df["question"].iloc[idx],
                  "id": str(idx+1),
              }
          ],
      }
  ]
  answers, probabilities = model.predict(to_predict)
  question_list.append(query_df["question"].iloc[idx])
  file_list.append(query_df["file1"].iloc[idx])
  ans_list.append(answers[0]['answer'][0])  #get only first answer (highest probability)
  prob_list.append(probabilities[0]['probability'][0]) #highest probability

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 10280.16it/s]


Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 7084.97it/s]


Running Prediction:   0%|          | 0/2 [00:00<?, ?it/s]

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 9709.04it/s]


...

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 7476.48it/s]


Running Prediction:   0%|          | 0/4 [00:00<?, ?it/s]

add example index and unique id: 100%|██████████| 1/1 [00:00<00:00, 6168.09it/s]


Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
result = pd.DataFrame({
    'file':file_list,
    'question':question_list,
    'answers':ans_list,
    'prob':prob_list
})

In [ ]:
result

file                                           question  \
0    1345184.txt  ตลาดหลักทรัพย์ได้กำหนดราคาสูงสุดต่ำสุดของ Warr...   
1    1345182.txt                 ลักษณะแนวทางในการระดมทุนมีอะไรบ้าง   
2    1345143.txt  Gross Price หรือ Dirty Price มีวิธีการจ่ายดอกเ...   
3    1345172.txt  รายได้จากการลงทุนต่อ (Reinvestment income) คือ...   
4    1345196.txt  ตัวอย่างลำดับเหตุการณ์ที่เกี่ยวข้องกับการจ่ายเ...   
..           ...                                                ...   
270  1345159.txt  ผู้จัดอันดับกองทุนรวมที่ได้รับอนุญาตจาก ก.ล.ต....   
271  1345176.txt               สูตรการคำนวณ Cash Settlement คืออะไร   
272  1345153.txt      ข้อดีของการประเมินมูลค่าด้วย PB Ratio คืออะไร   
273  1345198.txt           การรวมหุ้น (Reverse Stock Split) คืออะไร   
274  1345189.txt    งบประจำงวด 1 ปี ฉบับตรวจสอบ กำหนดส่งภายในกี่วัน   

                                               answers      prob  
0    +30% ต่ำสุด -30% ของราคาปิดสินทรัพย์อ้างอิงวัน...  0.800296  
1                                                       1.000000  
2           รายเดือน, รายไตรมาส, ทุกครึ่งปี หรือ รายปี  0.791365  
3                  รายได้จากการนำดอกเบี้ยรับไปลงทุนต่อ  1.000000  
4    10 เม.ย.: บริษัทประกาศว่าจะจ่ายเงินปันผล ซึ่งบ...  0.998296  
..                                                 ...       ...  
270  1) FICTH Rating Thailand 2) Reuters Thailand 3...  0.965368  
271  ชำระส่วนต่างของราคาด้วยเงินสด อัตราการใช้สิทธิ...  0.467050  
272  * หาข้อมูลง่าย เนื่องจากเป็นที่นิยม ข้อจำกัด *...  0.317956  
273  การรวมมูลค่าของกิจการ ทำให้มีจำนวนหุ้นน้อยลงแต...  0.999648  
274  ภายใน 3 เดือน จากวันสิ้นสุดรอบระยะเวลาบัญชี (ไ...  0.467374  

[275 rows x 4 columns]

In [ ]:
number = [x for x in range(1,276)]

In [ ]:
result['id'] = number

In [ ]:
result_2 = result[['id','answers']]

In [ ]:
result_2 = result_2.rename(columns={'answers': 'answer'})

In [ ]:
sample_sub = pd.read_csv("/content/sample_submission.csv")
result_2 = result_2.merge(sample_sub, left_on="id", right_on="id", how="right")

In [ ]:
result_2 = result_2.drop('answer_y',axis=1)

In [ ]:
result_2 = result_2.rename(columns={'answer_x': 'answer'})

In [ ]:
result_2['answer'] = result_2['answer'] .fillna("")

In [ ]:
result_2

id                                             answer
0      1  +30% ต่ำสุด -30% ของราคาปิดสินทรัพย์อ้างอิงวัน...
1      2                                                   
2      3         รายเดือน, รายไตรมาส, ทุกครึ่งปี หรือ รายปี
3      4                รายได้จากการนำดอกเบี้ยรับไปลงทุนต่อ
4      5  10 เม.ย.: บริษัทประกาศว่าจะจ่ายเงินปันผล ซึ่งบ...
..   ...                                                ...
270  271  1) FICTH Rating Thailand 2) Reuters Thailand 3...
271  272  ชำระส่วนต่างของราคาด้วยเงินสด อัตราการใช้สิทธิ...
272  273  * หาข้อมูลง่าย เนื่องจากเป็นที่นิยม ข้อจำกัด *...
273  274  การรวมมูลค่าของกิจการ ทำให้มีจำนวนหุ้นน้อยลงแต...
274  275  ภายใน 3 เดือน จากวันสิ้นสุดรอบระยะเวลาบัญชี (ไ...

[275 rows x 2 columns]

In [ ]:
from google.colab import files
import pandas as pd
result_2.to_csv('final_submission_1.csv',index=False)
files.download('final_submission_1.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#mv '/content/outputs/best_model' '/content/drive/MyDrive/NLP/Final Model'